In [1]:
!git clone https://github.com/mueedurrehman/distiller.git
%cd distiller
!pip3 install -e .

Cloning into 'distiller'...
remote: Enumerating objects: 6163, done.
remote: Total 6163 (delta 0), reused 0 (delta 0), pack-reused 6163
Receiving objects: 100% (6163/6163), 39.81 MiB | 32.23 MiB/s, done.
Resolving deltas: 100% (4326/4326), done.
/content/distiller
Obtaining file:///content/distiller
     |████████████████████████████████| 2.1MB 8.1MB/s 
     |████████████████████████████████| 734.6MB 24kB/s 
     |████████████████████████████████| 10.2MB 40.9MB/s 
     |████████████████████████████████| 460kB 51.8MB/s 
     |████████████████████████████████| 110.5MB 35kB/s 
     |████████████████████████████████| 51kB 9.1MB/s 
     |████████████████████████████████| 798kB 42.3MB/s 
     |████████████████████████████████| 112kB 56.0MB/s 
     |████████████████████████████████| 1.7MB 53.4MB/s 
     |████████████████████████████████| 235kB 61.5MB/s 
     |████████████████████████████████| 153kB 54.7MB/s 
     |████████████████████████████████| 61kB 10.3MB/s 
     |████████████████████████

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
import torch
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from torchsummary import summary
import matplotlib.pyplot as plt
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import time
import math
import yaml
import distiller
from collections import OrderedDict
import os
import pandas as pd

In [ ]:
#fix your output directory issues. Song's paper on learning rates was IMPORTANT! else get 88% accuracies otherwise.

MSMGResults/2020.12.05-040722

In [3]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainMulti0.5.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-040722/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           1675 |    0.00000 |    0.00000 |  0.00000 | 30.56641 |  0.00000 |   81.82509 | 0.04966 | -0.00253 |    0.01985 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            931 |    0.00000 |    0.00000 |  0.00000 | 54.88281 |  0.00000 |   89.89800 | 0.03274 |  0.00067 |    0.00985 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1463 |    0.00000 |    0.00000 |  0.00000 | 38.76953 |  3.12500 |   84.12543 | 0.04357 | -0.00258 |    0.01629 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            952 |    0.00000 |    0.00000 |  3.12500 | 56.05469 |  0.00000 |   89.67014 | 0.03030 | -0.00033 |    0.00916 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           1838 |    0.00000 |    0.00000 |  0.00000 | 33.10547 |  9

In [4]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainExpLR.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-040722/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           1675 |    0.00000 |    0.00000 |  0.00000 | 30.56641 |  0.00000 |   81.82509 | 0.05074 | -0.00262 |    0.02034 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            931 |    0.00000 |    0.00000 |  0.00000 | 54.88281 |  0.00000 |   89.89800 | 0.03345 |  0.00071 |    0.01009 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1463 |    0.00000 |    0.00000 |  0.00000 | 38.76953 |  3.12500 |   84.12543 | 0.04444 | -0.00282 |    0.01666 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            952 |    0.00000 |    0.00000 |  3.12500 | 56.05469 |  0.00000 |   89.67014 | 0.03096 | -0.00028 |    0.00939 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           1838 |    0.00000 |    0.00000 |  0.00000 | 33.10547 |  9

MSMGResults/2020.12.05-013904

In [5]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainMulti0.5.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-013904/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           3876 |    0.00000 |    0.00000 |  0.00000 |  6.05469 |  0.00000 |   57.94271 | 0.05655 | -0.00499 |    0.03362 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           2100 |    0.00000 |    0.00000 |  0.00000 | 29.10156 |  0.00000 |   77.21354 | 0.03793 |  0.00037 |    0.01706 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           3265 |    0.00000 |    0.00000 |  0.00000 | 13.37891 |  0.00000 |   64.57248 | 0.04857 | -0.00472 |    0.02663 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           2815 |    0.00000 |    0.00000 |  0.00000 | 22.65625 |  0.00000 |   69.45530 | 0.03590 | -0.00032 |    0.01822 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3754 |    0.00000 |    0.00000 |  0.00000 | 13.37891 |  9

In [6]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainExpLR.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-013904/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           3876 |    0.00000 |    0.00000 |  0.00000 |  6.05469 |  0.00000 |   57.94271 | 0.05817 | -0.00506 |    0.03445 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           2100 |    0.00000 |    0.00000 |  0.00000 | 29.10156 |  0.00000 |   77.21354 | 0.03902 |  0.00045 |    0.01752 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           3265 |    0.00000 |    0.00000 |  0.00000 | 13.37891 |  0.00000 |   64.57248 | 0.04993 | -0.00502 |    0.02734 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           2815 |    0.00000 |    0.00000 |  0.00000 | 22.65625 |  0.00000 |   69.45530 | 0.03686 | -0.00042 |    0.01867 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3754 |    0.00000 |    0.00000 |  0.00000 | 13.37891 |  9

OneShotElementBaseNoOptResults/92.2-85.94

In [7]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainMulti0.5.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/OneShotElementBaseNoOptResults/92.2-85.94/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           2765 |    0.00000 |    0.00000 |  0.00000 | 15.52734 |  0.00000 |   69.99783 | 0.05703 | -0.00407 |    0.02806 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            922 |    0.00000 |    0.00000 |  0.00000 | 58.59375 |  0.00000 |   89.99566 | 0.03383 |  0.00141 |    0.00985 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           2304 |    0.00000 |    0.00000 |  0.00000 | 26.66016 |  3.12500 |   75.00000 | 0.04879 | -0.00346 |    0.02191 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            922 |    0.00000 |    0.00000 |  6.25000 | 60.93750 |  0.00000 |   89.99566 | 0.03068 |  0.00018 |    0.00887 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3226 |    0.00000 |    0.00000 |  0.00000 | 17.28516 |  9

In [8]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainExpLR.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/OneShotElementBaseNoOptResults/92.2-85.94/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           2765 |    0.00000 |    0.00000 |  0.00000 | 15.52734 |  0.00000 |   69.99783 | 0.05820 | -0.00398 |    0.02872 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            922 |    0.00000 |    0.00000 |  0.00000 | 58.59375 |  0.00000 |   89.99566 | 0.03452 |  0.00159 |    0.01003 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           2304 |    0.00000 |    0.00000 |  0.00000 | 26.66016 |  3.12500 |   75.00000 | 0.04977 | -0.00356 |    0.02231 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            922 |    0.00000 |    0.00000 |  6.25000 | 60.93750 |  0.00000 |   89.99566 | 0.03126 |  0.00011 |    0.00907 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3226 |    0.00000 |    0.00000 |  0.00000 | 17.28516 |  9

MSMGResults/2020.12.05-043730

In [9]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainMulti0.5.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-043730/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           1568 |    0.00000 |    0.00000 |  0.00000 | 31.15234 |  0.00000 |   82.98611 | 0.04922 | -0.00246 |    0.01896 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            857 |    0.00000 |    0.00000 |  0.00000 | 56.93359 |  0.00000 |   90.70095 | 0.03253 |  0.00102 |    0.00930 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1364 |    0.00000 |    0.00000 |  0.00000 | 40.42969 |  3.12500 |   85.19965 | 0.04337 | -0.00281 |    0.01558 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            874 |    0.00000 |    0.00000 |  3.12500 | 57.42188 |  0.00000 |   90.51649 | 0.03017 | -0.00016 |    0.00870 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           1700 |    0.00000 |    0.00000 |  0.00000 | 34.86328 |  9

In [10]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/RetrainOnly/retrainExpLR.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults/2020.12.05-043730/best.pth.tar" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/TuningExperiments" --epochs 100 --vs=0 --lr=0.05

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           1568 |    0.00000 |    0.00000 |  0.00000 | 31.15234 |  0.00000 |   82.98611 | 0.05019 | -0.00238 |    0.01930 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            857 |    0.00000 |    0.00000 |  0.00000 | 56.93359 |  0.00000 |   90.70095 | 0.03324 |  0.00095 |    0.00953 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1364 |    0.00000 |    0.00000 |  0.00000 | 40.42969 |  3.12500 |   85.19965 | 0.04440 | -0.00278 |    0.01595 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            874 |    0.00000 |    0.00000 |  3.12500 | 57.42188 |  0.00000 |   90.51649 | 0.03086 | -0.00006 |    0.00888 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           1700 |    0.00000 |    0.00000 |  0.00000 | 34.86328 |  9